# Assignment 4: "Search your transcripts. You will know it to be true."

© Cristian Danescu-Niculescu-Mizil 2023

<p style="text-align:center">
    <img src="https://imgs.xkcd.com/comics/mainly_known_for.png" alt="xkcd Mainly Known For: Oh sure, I know Keira Knightly, from the first movie in that series by The Land Before Time producer. You know, the franchise with the guy from Jurassic Park and Ghostwriter, and script work by Billie Lourd's mom?" width="650"/><br/>(source: <a href="https://xkcd.com/2621">https://xkcd.com/2621</a>)
</p>

## CS/INFO 4300 Language and Information<a class="anchor" id="guidelines"></a>


<font color='red'>

**DUE**: February 22, 2023 (Wednesday), 11:59pm
    
</font>

<font color='purple'> 
    
**EXTRA CREDIT QUESTION** due: February 24th, 2023 (Friday), 11:59pm (separate CMS submission, same notebook)

</font>

This is an **individual** assignment. 

If you use any outside sources (e.g. research papers, StackOverflow) please list your sources.

Need to find out the full name of "steve pixar guy"? Or perhaps you want to know the identity of "song guy from labyrinth"? Sounds like what you need is a system that can efficiently search through large collections of documents!

In class, we have seen a number of techniques useful for searching through collections of documents, including edit distance and cosine similarity. Our overall goal in this assignment is to apply these techniques to build a system that efficiently searches for documents similar to a query in large data sets. We will explore the tradeoffs of information retrieval systems by finding newspaper quotes from "Keeping Up With The Kardashians".

**Guidelines**

All cells that contain the blocks that read `# YOUR CODE HERE` are editable and are to be completed to ensure you pass the test-cases. Make sure to write your code where indicated.

All cells that read `YOUR ANSWER HERE` are free-response cells that are editable and are to be completed.

You may use any number of notebook cells to explore the data and test out your functions, although you will only be graded on the solution itself.

You are unable to modify the read-only cells and should never delete any of the given cells.

You should also use Markdown cells to explain your code and discuss your results when necessary.
Instructions can be found [here](http://jupyter-notebook.readthedocs.io/en/latest/examples/Notebook/Working%20With%20Markdown%20Cells.html).

All floating point values should be printed with **2 decimal places** precision. You can do so using the built-in round function.

Unless otherwise stated, no cell in this assignment should take longer than **1 second** to run. If a cell takes longer than 1 second to run, it will be marked as incorrect.

**Grading**

For code-completion questions you will be graded on passing the public test cases we have included, as well as any hidden test cases that we have supplemented to ensure that your logic is correct.

For free-response questions you will be manually graded on the quality of your answer.

**Learning Objectives**
- Examine how edit distance can be applied as a search metric
- Develop an understanding of the inverted index and its applications
- Explore use cases of boolean search
- Examine how the inverted index can be used to efficiently compute IDF values
- Introduce cosine similarity as an efficient search model

- - -
### Contents  <a class="anchor" id="contents"></a>

* [Instructions and guidelines](#guidelines)
* [Contents](#contents)
* [Imports and Motivations](#imports)


* [[**Minimum Edit Distance**]](#part1)
  * [Imports and data](#0)
  * [[1](#q1a)] Levenshtein Edit Distance
    * [[1a](#q1a)] Levenshtein Edit Distance
    * [[1b](#q1b)] Query Discussion and Analysis
  * [[2](#q2a)] Change Levenshtein Edit Distance Costs
    * [[2a](#q2a)] Changing the costs
    * [[2b](#q2b)] Query Discussion and Analysis
    
* [[**Cosine Similarity**]](#part2)
  * [[3](#q3)] Inverted Index
    * [[3](#q3)] Write a function to construct the inverted index
  * [[4](#q4a)] Inverted Index and Boolean Search
    * [[4a](#q4a)] Using the inverted index for boolean search
    * [[4b](#q4b)] Using the inverted index for boolean search
  * [[5](#q5)] Inverted Index and IDF
    * [[5](#q5)] Compute IDF using the inverted index
  * [[6](#q6)] Inverted Index and Norm of Document
    * [[6](#q6)] Compute the norm of each document using the inverted index
  * [[7](#q7)] Inverted Index and Dot Product
    * [[7](#q7)] Efficiently compute the dot product using the inverted index
  * [[8](#q8)] Similar Message Finder
    * [[8a](#q8)] Find the most similar messages to the quotes
    * [[8b](#q8b)] Find the most similar messages to the quotes analysis
    
* [[**Extra Credit (optional)**]](#ec)  
  * [[9](#q9)] Finding your own similarity metric


(For those curious, the rendering of backlink to "contents" from each section, i.e., the right corner [[contents](#contents)] link, is only accessible via .ipynb notebook, it causes unexpected behavior when viewed in .html.)

### Imports <a class="anchor" id="imports"></a>

In [1]:
from collections import defaultdict
from collections import Counter
import json
import math
import string
import time
import numpy as np
from nltk.tokenize import TreebankWordTokenizer
from IPython.core.display import HTML

In [2]:
with open("kardashian-transcripts.json", "r") as f:
    transcripts = json.load(f)
print(len(transcripts[0]))

851


# Find Most Similar Messages

## Motivation

The tabloids have been going crazy over our stars! The press took some  quotes from the show, including:
       
 - *"It's like a bunch of people running around talking about nothing."*
 - *"Never say to a famous person that this possible endorsment would bring 'er to the spot light."*
 - *"Your yapping is making my head ache!"*
 - *"I'm going to Maryland, did I tell you?"*
 
We need to find out who said each of these, and in which episode. But since we're information scientists, that's not enough. We want to build an efficient search engine for retrieving where such quotes come from in the future.

What makes this difficult is that journalists often modify the quotes, so exact matching will not always work.

In [3]:
treebank_tokenizer = TreebankWordTokenizer()
flat_msgs = [m for transcript in transcripts for m in transcript]
queries = [u"It's like a bunch of people running around talking about nothing.",
           u"Never say to a famous person that this possible endorsment would bring 'er to the spot light.",
           u"Your yapping is making my head ache!",
           u"I'm going to Maryland, did I tell you?"]

In [4]:
flat_msgs

[{'episode_title': 'Keeping Up With the Kardashians - Shape Up or Ship Out',
  'speaker': 'KHLOE',
  'text': "You don't have your own credit card?",
  'timestamp': '00:00:23',
  'toks': ['you', 'do', "n't", 'have', 'your', 'own', 'credit', 'card', '?'],
  'transcript_id': 'kardashians/153890'},
 {'episode_title': 'Keeping Up With the Kardashians - Shape Up or Ship Out',
  'speaker': 'BRUCE',
  'text': "I don't even have a credit card.",
  'timestamp': '00:00:25',
  'toks': ['i', 'do', "n't", 'even', 'have', 'a', 'credit', 'card', '.'],
  'transcript_id': 'kardashians/153890'},
 {'episode_title': 'Keeping Up With the Kardashians - Shape Up or Ship Out',
  'speaker': 'BRUCE',
  'text': 'I know.',
  'timestamp': '00:00:26',
  'toks': ['i', 'know', '.'],
  'transcript_id': 'kardashians/153890'},
 {'episode_title': 'Keeping Up With the Kardashians - Shape Up or Ship Out',
  'speaker': 'KHLOE',
  'text': 'You are such a little girl.',
  'timestamp': '00:00:27',
  'toks': ['you', 'are', 'such

- - -
<p style='text-align:right; font-size:11px'>[[contents](#contents)]</p>

## Minimum Edit Distance<a class="anchor" id="part1"></a>

### Q1a: Levenshtein Edit Distance (Code Completion)<a class="anchor" id="q1a"></a>

From class and previous assignments, you have learned several methods of comparing similarities between text. Here, we will now first try using the edit distance metric (Levenshtein) to see how it compares the query text with our dataset. For each query, we will need to loop over each message, and compute the edit distance each time, there are no obvious shortcuts. (The code will take some time to run!)

We've provided you with code to compute the edit matrix that we discussed in class. You will need to complete the code stub below. (You can refer to the worksheet we used in class if you need a refresher on how this works.)

Note that instead of directly coding the insertion, deletion, and substitution costs into the edit matrix code, we've designed the code to take three *functions* as parameters to compute each cost. You'll see why we did it this way once you get to the next question! As in previous assignments, make sure to use these parameters; you will lose points if you hard-code the costs or reference global variables!

Note: It is ok for there to be duplicates in your results.

In [5]:
def insertion_cost(message, j):
    return 1

def deletion_cost(query, i):
    return 1

def substitution_cost(query, message, i, j):
    if query[i-1] == message[j-1]:
        return 0
    else:
        return 1

def edit_matrix(query, message, ins_cost_func, del_cost_func, sub_cost_func):
    """ Calculates the edit matrix
    
    Arguments
    =========
    
    query: query string,
        
    message: message string,
    
    ins_cost_func: function that returns the cost of inserting a letter,
    
    del_cost_func: function that returns the cost of deleting a letter,
    
    sub_cost_func: function that returns the cost of substituting a letter,
    
    Returns:
        edit matrix {(i,j): int}
    """
    
    m = len(query) + 1
    n = len(message) + 1

    chart = {(0, 0): 0}
    for i in range(1, m): 
        chart[i,0] = chart[i-1, 0] + del_cost_func(query, i) 
    for j in range(1, n): 
        chart[0,j] = chart[0, j-1] + ins_cost_func(message, j)
    for i in range(1, m):
        for j in range(1, n):
            chart[i, j] = min(
                chart[i-1, j] + del_cost_func(query, i),
                chart[i, j-1] + ins_cost_func(message, j),
                chart[i-1, j-1] + sub_cost_func(query, message, i, j)
            )
    return chart

def edit_distance(query, message, ins_cost_func, del_cost_func, sub_cost_func):
    """ Finds the edit distance between a query and a message using the edit matrix
    
    Arguments
    =========
    
    query: query string,
        
    message: message string,
    
    ins_cost_func: function that returns the cost of inserting a letter,
    
    del_cost_func: function that returns the cost of deleting a letter,
    
    sub_cost_func: function that returns the cost of substituting a letter,
    
    Returns:
        edit cost (int)
    """
        
    query = query.lower()
    message = message.lower()
    
    len_query = len(query)
    len_message = len(message)
    edit_matrix(query, message, ins_cost_func, del_cost_func, sub_cost_func)
    return edit_matrix(query, message, ins_cost_func, del_cost_func, sub_cost_func)[len_query, len_message]


def edit_distance_search(query, msgs, ins_cost_func, del_cost_func, sub_cost_func):
    """ Edit distance search
    
    Arguments
    =========
    
    query: string,
        The query we are looking for.
        
    msgs: list of dicts,
        Each message in this list has a 'text' field with
        the raw document.
        
    ins_cost_func: function that returns the cost of inserting a letter,
    
    del_cost_func: function that returns the cost of deleting a letter,
    
    sub_cost_func: function that returns the cost of substituting a letter,
    
    Returns
    =======
    
    result: list of (score, message) tuples.
        The result list is sorted by score such that the closest match
        is the top result in the list.
    
    """
    result = []
    for msg in msgs:
        score = edit_distance(query, msg['text'], ins_cost_func, del_cost_func, sub_cost_func)
        result.append((score, msg))

    return sorted(result, key=lambda x: x[0])

In [6]:
flat_msgs[0]

{'episode_title': 'Keeping Up With the Kardashians - Shape Up or Ship Out',
 'speaker': 'KHLOE',
 'text': "You don't have your own credit card?",
 'timestamp': '00:00:23',
 'toks': ['you', 'do', "n't", 'have', 'your', 'own', 'credit', 'card', '?'],
 'transcript_id': 'kardashians/153890'}

In [7]:
edit_distance(queries[0], flat_msgs[0]['text'], insertion_cost, deletion_cost, substitution_cost)

52

**NOTE**: Autograder tests for this function may take a few minutes to execute.

In [8]:
# # This is an autograder test. Here we can test the function you just wrote above.
# score, _ = edit_distance_search(queries[1], flat_msgs, insertion_cost, deletion_cost, substitution_cost)[0]
# assert score == 42


When the edit_distance_search function is completed you can run the lines below to print out the best matches for each query string. **NOTE**: This cell will take a few minutes to execute.

In [9]:
# # note: this will take about 1-2 minutes to execute
# top_10 = []
# for query in queries:
#     print("#" * len(query))
#     print(query)
#     print("#" * len(query))

#     for score, msg in edit_distance_search(query, flat_msgs, insertion_cost, deletion_cost, substitution_cost)[:10]:
#         print("[{:.2f}] {}: {}\n\t({})".format(
#             score,
#             msg['speaker'],
#             msg['text'],
#             msg['episode_title']))
#         top_10.append(msg)
#     print()

top_10 = [{'toks': ['it', "'s", 'like', 'a', 'bunch', 'of', 'people', 'running', 'around', 'talking', 'about', 'nothing', '.'], 'text': "It's like a bunch of people running around talking about nothing.", 'episode_title': "Keeping Up With the Kardashians - Kourt's First Cover", 'transcript_id': 'kardashians2/254473', 'speaker': 'BRUCE', 'timestamp': '00:18:20'}, {'toks': ['it', "'s", 'not', 'a', 'bunch', 'of', 'teenagers', 'running', 'around', '.'], 'text': "It's not a bunch of teenagers running around.", 'episode_title': "Keeping Up With the Kardashians - Kris ``The Cougar'' Jenner", 'transcript_id': 'kardashians2/487096', 'speaker': 'KRIS', 'timestamp': '00:19:09'}, {'toks': ['it', "'s", 'like', ',', 'what', 'are', 'you', 'talking', 'about', '?'], 'text': "It's like, what are you talking about?", 'episode_title': 'The Wedding: Keeping Up With the Kardashians', 'transcript_id': 'kardashians3/215847', 'speaker': 'KHLOE', 'timestamp': '01:45:24'}, {'toks': ['it', "'s", 'like', 'it', 'has', 'separation', 'anxiety', 'or', 'something', '.'], 'text': "It's like it has separation anxiety or something.", 'episode_title': 'Keeping Up With the Kardashians - Shape Up or Ship Out', 'transcript_id': 'kardashians/162959', 'speaker': 'KIM', 'timestamp': '00:56:01'}, {'toks': ['it', "'s", 'like', 'i', 'want', 'to', 'learn', 'how', 'to', 'do', 'that', '.'], 'text': "It's like I want to learn how to do that.", 'episode_title': 'Keeping Up With the Kardashians - Distance Makes the Heart Grow Fonder', 'transcript_id': 'kardashians2/202352', 'speaker': 'KHLOE', 'timestamp': '00:04:16'}, {'toks': ['it', "'s", 'like', 'an', 'explosion', 'in', 'your', 'pantyhose', '.'], 'text': "It's like an explosion in your pantyhose.", 'episode_title': "Keeping Up With the Kardashians - I'd Rather Go Naked... Or Shopping", 'transcript_id': 'kardashians2/332117', 'speaker': 'KOURTNEY', 'timestamp': '00:28:21'}, {'toks': ['i', 'have', 'a', 'bunch', 'of', 'connections', 'in', 'the', 'industry', '.'], 'text': 'I have a bunch of connections in the industry.', 'episode_title': 'Keeping Up With the Kardashians - Must Love Dogs', 'transcript_id': 'kardashians2/164513', 'speaker': 'ROB', 'timestamp': '00:15:37'}, {'toks': ['i', 'have', 'a', 'bunch', 'of', 'connections', 'in', 'the', 'industry', '.'], 'text': 'I have a bunch of connections in the industry.', 'episode_title': 'Keeping Up With the Kardashians - Must Love Dogs', 'transcript_id': 'kardashians2/164513', 'speaker': 'ROB', 'timestamp': '00:15:18'}, {'toks': ['that', "'s", 'why', 'you', "'re", 'running', 'around', 'wearing', 'black', '.'], 'text': "That's why you're running around wearing black.", 'episode_title': "Keeping Up With the Kardashians - I'd Rather Go Naked... Or Shopping", 'transcript_id': 'kardashians2/332117', 'speaker': 'BRUCE', 'timestamp': '00:01:32'}, {'toks': ['that', "'s", 'why', 'you', "'re", 'running', 'around', 'wearing', 'black', '.'], 'text': "That's why you're running around wearing black.", 'episode_title': "Keeping Up With the Kardashians - Kourt's First Cover", 'transcript_id': 'kardashians2/507032', 'speaker': 'BRUCE', 'timestamp': '00:29:08'}, {'toks': ['you', 'do', "n't", 'tell', 'an', 'international', 'celebrity', 'that', 'this', 'possible', 'endorsement', 'could', 'bring', 'her', 'back', 'into', 'the', 'spotlight', '.'], 'text': "You don't tell an international celebrity that this possible endorsement could bring her back into the spotlight.", 'episode_title': 'Keeping Up With the Kardashians - Delivering Baby Mason', 'transcript_id': 'kardashians2/209686', 'speaker': 'SIMON', 'timestamp': '00:23:30'}, {'toks': ['you', 'need', 'to', 'trust', 'that', 'i', 'actually', 'know', 'what', 'i', "'m", 'doing', 'at', 'some', 'point', '.'], 'text': "You need to trust that I actually know what I'm doing at some point.", 'episode_title': 'Keeping Up With the Kardashians - Blame It on the Alcohol', 'transcript_id': 'kardashians2/213003', 'speaker': 'KRIS', 'timestamp': '00:44:16'}, {'toks': ['you', 'know', ',', 'i', "'ve", 'seen', 'her', 'do', 'this', 'before', ',', 'and', 'it', "'s", 'just', 'not', 'right', '.'], 'text': "You know, I've seen her do this before, and it's just not right.", 'episode_title': 'Keeping Up With the Kardashians - Baby Blues', 'transcript_id': 'kardashians2/166360', 'speaker': 'BRUCE', 'timestamp': '00:07:42'}, {'toks': ['i', 'feel', 'like', 'people', 'want', 'to', 'see', 'you', ',', 'like', ',', 'back', 'in', 'the', 'spotlight', '.'], 'text': 'I feel like people want to see you, like, back in the spotlight.', 'episode_title': 'Keeping Up With the Kardashians - Delivering Baby Mason', 'transcript_id': 'kardashians2/209686', 'speaker': 'ALEX', 'timestamp': '00:23:26'}, {'toks': ['trust', 'me', ',', 'this', 'is', 'the', 'most', 'entertaining', 'part', 'of', 'the', 'entire', 'night', '.'], 'text': 'Trust me, this is the most entertaining part of the entire night.', 'episode_title': 'Keeping Up With the Kardashians - Birthday Suit', 'transcript_id': 'kardashians2/236786', 'speaker': 'KHLOE', 'timestamp': '00:24:29'}, {'toks': ['i', 'clean', 'all', 'the', 'counters', 'at', 'like', 'from', 'the', 'floors', 'to', 'the', 'bathtub', 'to', 'the', 'toilet', '.'], 'text': 'I clean all the counters at like from the floors to the bathtub to the toilet.', 'episode_title': "Keeping Up With the Kardashians - Kim's Calendar for Reggie", 'transcript_id': 'kardashians2/332078', 'speaker': 'ROB', 'timestamp': '00:17:03'}, {'toks': ['i', 'did', "n't", 'want', 'to', 'go', 'on', 'this', 'trip', 'and', 'i', "'m", 'not', 'talking', 'to', 'them', 'at', 'all', '.'], 'text': "I didn't want to go on this trip and I'm not talking to them at all.", 'episode_title': 'Keeping Up With the Kardashians - Kardashian Civil War', 'transcript_id': 'kardashians2/514446', 'speaker': 'KIM', 'timestamp': '00:07:15'}, {'toks': ['i', 'reminded', 'you', 'this', 'morning', 'that', 'you', 'needed', 'to', 'bring', 'the', 'designs', '.'], 'text': 'I reminded you this morning that you needed to bring the designs.', 'episode_title': 'Keeping Up With the Kardashians - Family vs. Money', 'transcript_id': 'kardashians2/597452', 'speaker': 'ELIZABETH', 'timestamp': '00:18:25'}, {'toks': ['okay.', 'if', 'it', 'was', 'you', 'against', 'the', 'other', 'three', ',', 'i', 'would', 'have', 'felt', 'the', 'same', 'way', '.'], 'text': 'Okay. If it was you against the other three, I would have felt the same way.', 'episode_title': 'Keeping Up With the Kardashians - Kardashian Civil War', 'transcript_id': 'kardashians2/59978', 'speaker': 'KRIS', 'timestamp': '00:15:16'}, {'toks': ['we', "'re", 'gon', 'na', 'take', 'a', 'look', 'at', 'these', 'polaroids', ',', 'and', 'then', 'we', "'ll", 'be', 'right', 'with', 'you', '.'], 'text': "We're gonna take a look at these Polaroids, and then we'll be right with you.", 'episode_title': "Keeping Up With the Kardashians - Khloe's Blind Dates", 'transcript_id': 'kardashians3/300212', 'speaker': 'DAVID', 'timestamp': '00:16:37'}, {'toks': ['your', 'yappity', 'voice', 'is', 'giving', 'me', 'a', 'headache', '!'], 'text': 'Your yappity voice is giving me a headache!', 'episode_title': 'Keeping Up With the Kardashians - Shape Up or Ship Out', 'transcript_id': 'kardashians/153890', 'speaker': 'KIM', 'timestamp': '00:35:19'}, {'toks': ['your', 'yappity', 'voice', 'is', 'giving', 'me', 'a', 'headache', '!'], 'text': 'Your yappity voice is giving me a headache!', 'episode_title': 'Keeping Up With the Kardashians - Shape Up or Ship Out', 'transcript_id': 'kardashians/153950', 'speaker': 'KIM', 'timestamp': '00:35:18'}, {'toks': ['you', 'want', 'to', 'make', 'peace', '?'], 'text': 'You want to make peace?', 'episode_title': 'Keeping Up With the Kardashians - Family vs. Money', 'transcript_id': 'kardashians2/597452', 'speaker': 'KIM', 'timestamp': '00:00:29'}, {'toks': ['everything', "'s", 'going', 'to', 'be', 'fine', '.'], 'text': "Everything's going to be fine.", 'episode_title': 'Keeping Up With the Kardashians - The Missing Ring', 'transcript_id': 'kardashians2/440790', 'speaker': 'BRUCE', 'timestamp': '00:04:17'}, {'toks': ['you', 'are', 'walking', 'me', 'me', 'down', '...'], 'text': 'You are walking me me down...', 'episode_title': 'Keeping Up With the Kardashians - The Wedding', 'transcript_id': 'kardashians2/520783', 'speaker': 'KHLOE', 'timestamp': '00:05:01'}, {'toks': ['you', 'are', 'walking', 'me', 'me', 'down', '...'], 'text': 'You are walking me me down...', 'episode_title': 'The Wedding: Keeping Up With the Kardashians', 'transcript_id': 'kardashians3/106185', 'speaker': 'KHLOE', 'timestamp': '00:26:07'}, {'toks': ['you', "'re", 'going', 'to', 'make', 'a', 'scene', '.'], 'text': "You're going to make a scene.", 'episode_title': "Keeping Up With the Kardashians - What's Yours Is Mine", 'transcript_id': 'kardashians3/75119', 'speaker': 'KRIS', 'timestamp': '00:15:49'}, {'toks': ['you', "'re", 'diving', 'in', 'for', 'the', 'cash', '?'], 'text': "You're diving in for the cash?", 'episode_title': 'Keeping Up With the Kardashians - Shape Up or Ship Out', 'transcript_id': 'kardashians/153890', 'speaker': 'BRUCE', 'timestamp': '00:00:51'}, {'toks': ['your', 'secret', 'is', 'safe', 'with', 'me', '.'], 'text': 'Your secret is safe with me.', 'episode_title': 'Keeping Up With the Kardashians - Shape Up or Ship Out', 'transcript_id': 'kardashians/153890', 'speaker': 'KHLOE', 'timestamp': '00:01:14'}, {'toks': ['you', "'re", 'diving', 'in', 'for', 'the', 'cash', '?'], 'text': "You're diving in for   the  cash?", 'episode_title': 'Keeping Up With the Kardashians - Shape Up or Ship Out', 'transcript_id': 'kardashians/153950', 'speaker': 'BRUCE', 'timestamp': '00:00:51'}, {'toks': ['i', "'m", 'going', 'to', 'go', 'play', 'with', 'rob', '.'], 'text': "I'm going to go play with Rob.", 'episode_title': 'Keeping Up With the Kardashians - Blind Date', 'transcript_id': 'kardashians2/522275', 'speaker': 'LAMAR', 'timestamp': '00:23:45'}, {'toks': ['i', "'m", 'going', 'to', 'move', 'to', 'new', 'york', '.'], 'text': "I'm going to move to New York.", 'episode_title': 'Keeping Up With the Kardashians - Distance Makes the Heart Grow Fonder', 'transcript_id': 'kardashians2/202352', 'speaker': 'KHLOE', 'timestamp': '00:07:36'}, {'toks': ['i', "'m", 'going', 'to', 'have', 'six', 'or', 'seven', '?'], 'text': "I'm going to have six or seven?", 'episode_title': 'Keeping Up With the Kardashians - The Wedding', 'transcript_id': 'kardashians2/520783', 'speaker': 'SCOTT', 'timestamp': '00:22:53'}, {'toks': ['i', "'m", 'going', 'to', 'move', 'to', 'new', 'york', '.'], 'text': "I'm going to move to New York.", 'episode_title': 'Keeping Up With the Kardashians - Free Khloe', 'transcript_id': 'kardashians2/59945', 'speaker': 'KHLOE', 'timestamp': '00:29:18'}, {'toks': ['i', "'m", 'going', 'to', 'have', 'six', 'or', 'seven', '?'], 'text': "I'm going to have six or seven?", 'episode_title': 'The Wedding: Keeping Up With the Kardashians', 'transcript_id': 'kardashians3/106185', 'speaker': 'SCOTT', 'timestamp': '00:43:59'}, {'toks': ['i', "'m", 'going', 'to', 'lunch', 'with', 'lisa', '.'], 'text': "I'm going to lunch with Lisa.", 'episode_title': 'The Wedding: Keeping Up With the Kardashians', 'transcript_id': 'kardashians3/152397', 'speaker': 'KRIS', 'timestamp': '00:59:03'}, {'toks': ['i', "'m", 'going', 'to', 'get', 'canned', 'inside', '.'], 'text': "I'm going to get canned inside.", 'episode_title': 'Keeping Up With the Kardashians - Shape Up or Ship Out', 'transcript_id': 'kardashians/162959', 'speaker': 'FRIEND', 'timestamp': '00:57:57'}, {'toks': ['i', "'m", 'going', 'to', 'get', 'canned', 'inside', '.'], 'text': "I'm going to get canned inside.", 'episode_title': 'Keeping Up With the Kardashians - Shape Up or Ship Out', 'transcript_id': 'kardashians/164454', 'speaker': 'FRIEND', 'timestamp': '00:57:59'}, {'toks': ['i', "'m", 'going', 'to', 'tell', 'her', '.'], 'text': "I'm going to tell her.", 'episode_title': 'Keeping Up With the Kardashians - Meet the Kardashians', 'transcript_id': 'kardashians2/202385', 'speaker': 'ROB', 'timestamp': '00:28:45'}, {'toks': ['i', "'m", 'going', 'to', 'need', 'it', '.'], 'text': "I'm going to need it.", 'episode_title': 'Keeping Up With the Kardashians - I Want Your Sex', 'transcript_id': 'kardashians2/238492', 'speaker': 'LAMAR', 'timestamp': '00:11:17'}]

### Q1b: Query Discussion and Analysis (Free Response)<a class="anchor" id="q1b"></a>

What do you notice about the search above?
1. Discuss why it worked, or why it might not have worked, for each query. 

2. Do you notice anything different about the costs to those discussed in lecture? 

3. Please fill out the table below with the costs from running the Levenshtein algorithm discussed in lecture and the cost from using the edit_distance function we provided above. Copy-and-paste this markdown table into the cell below for your answers:
```
| Operation    | Cost (Lecture)|  Cost (edit_distance)  | Example
| :----------: |:------------- | :-------------------------- | --------
| Addition     | YOUR ANSWER   | YOUR ANSWER                 | "aa" -> "aab"
| Deletion     | YOUR ANSWER   | YOUR ANSWER                 | "aa" -> "a"
| None         | YOUR ANSWER   | YOUR ANSWER                 | "aa" -> "aa"
| Substitution | YOUR ANSWER   | YOUR ANSWER                 | "aa" -> "ab"
| Multiple     | YOUR ANSWER   | YOUR ANSWER                 | "trawl" --> "claw"
```

YOUR ANSWER HERE

### Q2a: Changing the costs (Code Completion)<a class="anchor" id="q2a"></a>

The above implementation has been using standard costs as we did in class. Sometimes we might want to alter the edit-distance penalty depending on the type of change we are making. In practice, the use of a simple uniform cost for all changes is suboptimal, since certain changes are more likely to happen than others. For instance, it is easier to mix up characters that are adjacent to each other on the keyboard (typos), and we'd like you to **reduce the cost of such substitutions of adjacent keyboard letters to 1.5 instead of 2**. You should use the provided list of adjacent keyboard letters, found below.

In [10]:
# we provide you with a list of adjacent characters
adj_chars = [('a', 'q'), ('a', 's'), ('a', 'z'), ('b', 'g'), ('b', 'm'), ('b', 'n'), ('b', 'v'), ('c', 'd'),
             ('c', 'v'), ('c', 'x'), ('d', 'c'), ('d', 'e'), ('d', 'f'), ('d', 's'), ('e', 'd'), ('e', 'r'),
             ('e', 'w'), ('f', 'd'), ('f', 'g'), ('f', 'r'), ('f', 'v'), ('g', 'b'), ('g', 'f'), ('g', 'h'),
             ('g', 't'), ('h', 'g'), ('h', 'j'), ('h', 'm'), ('h', 'n'), ('h', 'y'), ('i', 'k'), ('i', 'o'),
             ('i', 'u'), ('j', 'h'), ('j', 'k'), ('j', 'u'), ('k', 'i'), ('k', 'j'), ('k', 'l'), ('l', 'k'),
             ('l', 'o'), ('m', 'b'), ('m', 'h'), ('n', 'b'), ('n', 'h'), ('o', 'i'), ('o', 'l'), ('o', 'p'),
             ('p', 'o'), ('q', 'a'), ('q', 'w'), ('r', 'e'), ('r', 'f'), ('r', 't'), ('s', 'a'), ('s', 'd'),
             ('s', 'w'), ('s', 'x'), ('t', 'g'), ('t', 'r'), ('t', 'y'), ('u', 'i'), ('u', 'j'), ('u', 'y'), 
             ('v', 'b'), ('v', 'c'), ('v', 'f'), ('w', 'e'), ('w', 'q'), ('w', 's'), ('x', 'c'), ('x', 's'), 
             ('x', 'z'), ('y', 'h'), ('y', 't'), ('y', 'u'), ('z', 'a'), ('z', 'x')]

In [13]:
def substitution_cost_adj(query, message, i, j):
    """
    Custom substitution cost:
    The cost is 1.5 when substituting a pair of characters that can be found in adj_chars
    Otherwise, the cost is 2. (Not 1 as it was before!)
    """
    if query[i-1] == message[j-1]:
        return 0
    elif (query[i-1], message[j-1]) in adj_chars:
        return 1.5
    else:
        return 2

In [14]:
assert edit_distance("Levenshtein","Levenstein", insertion_cost, deletion_cost, substitution_cost_adj) == 1
assert edit_distance("Levenshtein","Lebenshtein", insertion_cost, deletion_cost, substitution_cost_adj) == 1.5

Run the following code below to reorder the top ten closest matches for each query using our new custom edit-distance discounts. Once again, this may take a few minutes to run.

Note: It is ok to obtain duplicate results.

In [15]:
for query in queries:
    print("#" * len(query))
    print(query)
    print("#" * len(query))

    # we compare the query with top_10 to save time because
    # we already know that top_10 will be close to the query
    # so there is no need to check all flat_msgs
    for score, msg in edit_distance_search(query, top_10, insertion_cost, deletion_cost, substitution_cost_adj)[:10]:
        print("[{:.2f}] {}: {}\n\t({})".format(
            score,
            msg['speaker'],
            msg['text'],
            msg['episode_title']))
    print()

#################################################################
It's like a bunch of people running around talking about nothing.
#################################################################
[0.00] BRUCE: It's like a bunch of people running around talking about nothing.
	(Keeping Up With the Kardashians - Kourt's First Cover)
[39.50] KRIS: It's not a bunch of teenagers running around.
	(Keeping Up With the Kardashians - Kris ``The Cougar'' Jenner)
[42.00] KHLOE: It's like, what are you talking about?
	(The Wedding: Keeping Up With the Kardashians)
[45.00] KOURTNEY: It's like an explosion in your pantyhose.
	(Keeping Up With the Kardashians - I'd Rather Go Naked... Or Shopping)
[47.00] KHLOE: It's like I want to learn how to do that.
	(Keeping Up With the Kardashians - Distance Makes the Heart Grow Fonder)
[48.00] BRUCE: That's why you're running around wearing black.
	(Keeping Up With the Kardashians - I'd Rather Go Naked... Or Shopping)
[48.00] BRUCE: That's why you're running 

### Q2b: Query Discussion and Analysis (Free Response)<a class="anchor" id="q2b"></a>

4. How do the results after cost changes different compare to that of default `edit_distance` metric?

YOUR ANSWER HERE

- - -
<p style='text-align:right; font-size:11px'>[[contents](#contents)]</p>

## Cosine Similarity<a class="anchor" id="part2"></a>

### A high-level overview

Our overall goal of this assignment is to build a system where we can compute the text similarity between queries and our datasets quickly. From the previous part, we tried using variations of minimum edit distance as the metric. Now, we will try another method -- comparing two text through cosine similarity score. To accomplish queries and compute cosine similarities, as we learned in class, we will need to represent documents as ***vectors***! A common method of representing documents as vectors is by using "term frequency-inverse document frequency" (TF-IDF) scores. (Check the lecture modules on Canvas if you need a refresher). The notation here is consistent with the in-class hand out, so if you haven't read over it -- you should!

Consider the TF-IDF representation of a document and a query: $\vec{d_j}$ and $\vec{q}$, respectively. Elements of these vectors are very often zero because the term frequency of most words in most documents is zero. Stated differently, most words don't appear in most documents! Consider a query that has 5 words in it and a vocabulary that has 20K words in it -- only .025% of the elements of the vector representation of the query are nonzero! When a vector (or a matrix) has very few nonzero entries, it is called "sparse." We can take advantage of the sparsity of tf-idf document representations to compute cosine similarity quickly. We will first build some data stuctures that allow for faster querying of statistics, and then we will build a function that quickly computes cosine similarity between queries and documents.

### A starting point
We will use an **inverted index** for efficiency. This is a sparse term-centered representation that allows us to quickly find all documents that contain a given term.

### Q3 Write a function to construct the inverted index (Code Completion)<a class="anchor" id="q3"></a>

As in class, the inverted index is a key-value structure where the keys are terms and the values are lists of *postings*. In this case, we record the documents a term occurs in as well as the **count** of that term in that document.

In [80]:
def build_inverted_index(msgs):
    """ Builds an inverted index from the messages.
    
    Arguments
    =========
    
    msgs: list of dicts.
        Each message in this list already has a 'toks'
        field that contains the tokenized message.
    
    Returns
    =======
    
    inverted_index: dict
        For each term, the index contains 
        a sorted list of tuples (doc_id, count_of_term_in_doc)
        such that tuples with smaller doc_ids appear first:
        inverted_index[term] = [(d1, tf1), (d2, tf2), ...]
        
    Example
    =======
    
    >> test_idx = build_inverted_index([
    ...    {'toks': ['to', 'be', 'or', 'not', 'to', 'be']},
    ...    {'toks': ['do', 'be', 'do', 'be', 'do']}])
    
    >> test_idx['be']
    [(0, 2), (1, 2)]
    
    >> test_idx['not']
    [(0, 1)]
    
    """
    inverted_index = {}
    for doc_id, msg in enumerate(msgs):
        for term in msg['toks']:
            if term not in inverted_index:
                inverted_index[term] = []
            inverted_index[term].append((doc_id, msg['toks'].count(term)))
    
    for term in inverted_index:
        inverted_index[term] = sorted(list(set((inverted_index[term]))))
        
    
    return inverted_index

In [81]:
inv_idx = build_inverted_index(flat_msgs)
inv_idx['blah']

[(7439, 3), (12528, 3), (19035, 3), (19043, 3)]

In [82]:
# This is an autograder test. Here we can test the function you just wrote above.
start_time = time.time()
inv_idx = build_inverted_index(flat_msgs)
execution_time = time.time() - start_time

assert len(inv_idx) <= 10000 
assert [i[0] for i in inv_idx['bruce']] == sorted([i[0] for i in inv_idx['bruce']])
assert len(inv_idx['bruce']) < len(inv_idx['kim'])
assert len(inv_idx['bruce']) >= 400 and len(inv_idx['bruce']) <= 435
assert len(inv_idx['baby']) >= 250 and len(inv_idx['baby']) <= 300
assert execution_time <= 1.0


### Q4a Using the inverted index for boolean search (Code Completion)<a class="anchor" id="q4a"></a>

In this section we will use the inverted index you constructed to perform an efficient boolean search. The boolean model was one of the early information retrieval models, and continues to be used in applications today.

A boolean search works by searching for documents which match the boolean expression of the query. Three main operators in a boolean search are `AND` `OR` and `NOT`. For example, the query `"Ned" AND "Rob"` would return any document which contains both the words "Ned" and "Rob".

Here, we will treat a query as a simple two-word search with exclusion---that is, we will implement a search with `NOT` instead of `AND`. For example, the query words "kardashian", "kim" would be equivalent to the boolean expression `"kardashian" NOT "kim"`, and will return any document which contains the word "kardashian" while not containing the word "kim".

#### In class we implemented the Merge Postings Algorithm, review the code [here](https://colab.research.google.com/drive/1Egg26OyynPuWizjEhSzMJ4rad9TwFQ1s?usp=sharing).
Reminder: the algorithm takes two postings lists (A and B), then proceeds as follows:

------------------------------------------
Initialize empty list (called merged list M)

Start: Pointer at the first element of both A and B

Do: Does it point to the same document ID in each list?

    Yes: Append document ID to M, advance pointer in both A and B
    No: Advance (to the right) the pointer with the smaller ID
    
End: When we attempt to advance a pointer already at the end of its list

------------------------------------------

The above Merge Postings Algorithm can be thought of a boolean search with the `AND` operator. Write a function `boolean_search` that implements a similar algorithm with the `NOT` operator using the inverted index.

**Note:** Make sure you convert the `query_word` and `not_word` to lowercase. 


In [18]:
inv_idx

{'you': [(0, 1),
  (3, 1),
  (7, 1),
  (9, 1),
  (12, 1),
  (13, 1),
  (18, 1),
  (20, 1),
  (21, 1),
  (23, 2),
  (23, 2),
  (24, 1),
  (31, 1),
  (33, 1),
  (39, 1),
  (44, 1),
  (47, 2),
  (47, 2),
  (49, 1),
  (50, 1),
  (61, 1),
  (63, 1),
  (70, 1),
  (72, 1),
  (73, 3),
  (73, 3),
  (73, 3),
  (74, 1),
  (85, 1),
  (88, 1),
  (91, 1),
  (94, 1),
  (106, 1),
  (111, 1),
  (112, 1),
  (113, 1),
  (119, 1),
  (120, 1),
  (122, 1),
  (123, 2),
  (123, 2),
  (129, 1),
  (134, 1),
  (135, 1),
  (136, 1),
  (137, 1),
  (139, 1),
  (142, 1),
  (146, 1),
  (150, 1),
  (158, 1),
  (164, 1),
  (170, 2),
  (170, 2),
  (181, 1),
  (184, 1),
  (189, 1),
  (192, 1),
  (202, 1),
  (203, 1),
  (209, 1),
  (214, 2),
  (214, 2),
  (215, 1),
  (217, 1),
  (221, 1),
  (223, 1),
  (225, 1),
  (226, 1),
  (233, 2),
  (233, 2),
  (234, 1),
  (235, 1),
  (244, 1),
  (250, 1),
  (254, 1),
  (257, 1),
  (258, 2),
  (258, 2),
  (266, 1),
  (267, 1),
  (268, 1),
  (273, 1),
  (278, 1),
  (279, 1),
  (282, 1

In [19]:
def boolean_search(query_word,not_word, inverted_index):
    """ Search the collection of documents for the given query_word 
        provided that the documents do not include the not_word
    
    Arguments
    =========
    
    query_word: string,
        The word we are searching for in our documents.
    
    not_word: string,
        The word excluded from our documents.
    
    index: an inverted index as above
    
    
    Returns
    =======
    
    results: list of ints
        Sorted List of results (in increasing order) such that every element is a `doc_id`
        that points to a document that satisfies the boolean
        expression of the query.
        
    """
    results = []
    if query_word not in inverted_index:
        return results
    if not_word not in inverted_index:
        return [i[0] for i in inverted_index[query_word]]
    for i in inverted_index[query_word]:
        if i[0] not in [j[0] for j in inverted_index[not_word]]:
            results.append(i[0])
    return results

In [23]:
inv_idx['and']

[(15, 1),
 (23, 3),
 (23, 3),
 (23, 3),
 (27, 1),
 (34, 1),
 (35, 1),
 (47, 1),
 (49, 1),
 (50, 1),
 (58, 1),
 (66, 1),
 (72, 1),
 (73, 1),
 (91, 1),
 (93, 1),
 (96, 1),
 (106, 1),
 (109, 1),
 (119, 1),
 (123, 1),
 (124, 1),
 (135, 2),
 (135, 2),
 (146, 1),
 (152, 1),
 (166, 1),
 (167, 1),
 (170, 1),
 (173, 1),
 (175, 1),
 (195, 1),
 (215, 1),
 (234, 2),
 (234, 2),
 (247, 1),
 (256, 2),
 (256, 2),
 (263, 2),
 (263, 2),
 (264, 1),
 (280, 2),
 (280, 2),
 (281, 1),
 (300, 1),
 (303, 1),
 (308, 1),
 (314, 1),
 (316, 1),
 (321, 2),
 (321, 2),
 (323, 1),
 (325, 1),
 (327, 1),
 (342, 1),
 (350, 1),
 (352, 1),
 (364, 1),
 (366, 1),
 (372, 1),
 (382, 1),
 (385, 1),
 (389, 1),
 (391, 1),
 (392, 1),
 (399, 1),
 (403, 2),
 (403, 2),
 (409, 1),
 (439, 2),
 (439, 2),
 (443, 1),
 (454, 1),
 (459, 1),
 (484, 1),
 (490, 1),
 (506, 1),
 (508, 1),
 (510, 1),
 (515, 1),
 (541, 1),
 (560, 1),
 (564, 2),
 (564, 2),
 (566, 1),
 (586, 1),
 (599, 1),
 (603, 1),
 (605, 1),
 (623, 1),
 (627, 1),
 (634, 1),
 (659

In [20]:
result0_start_time = time.time()
result0 = boolean_search('ice','cream', inv_idx)
result0_execution_time = time.time() - result0_start_time
result3 = boolean_search('puppy','dog', inv_idx)
result1= boolean_search('Kardashian','Kim',inv_idx)
result4= boolean_search('cake','cake',inv_idx)
assert result0_execution_time < 1.0
assert type(result1) == list
assert len(result3) == 7
assert len(result4)==0


### Q4b Using the inverted index for boolean search (Free Response)<a class="anchor" id="q4b"></a>

Earlier in the assignment, we already explored search techniques (edit distance) which are able to find a wider variety of relevant results. Why might you want to use a boolean search with an inverted index instead? Justify your answer by explaining the difference between edit distance and boolean search with inverted index, *and* including at least one example where boolean search with inverted index would be a better choice than an edit distance search. **You will lose points if you do not provide an example!**

<div style="border-bottom: 4px solid #AAA; padding-bottom: 6px; font-size: 16px; font-weight: bold;">Write your answer in the provided cell below</div>

first of all, the edit distance is a technique that focuses on the similarity between sentences, always one-to-one correspondaence, whereas boolean search allows us to search with multiple inputs and there's interaction between words.  

In [58]:
boolean_search('anxiety','', inv_idx)

[1878, 9381, 14570, 15931, 16494, 19537, 24246, 27283, 31785, 34779]

<div style="border-top: 4px solid #AAA; padding-bottom: 6px; font-size: 16px; font-weight: bold; text-align: center;"></div>

### Q5 Compute IDF *using* the inverted index (Code Completion)<a class="anchor" id="q5"></a>

Write a function `compute_idf` that uses the inverted index to efficiently compute IDF values.

Words that occur in a very small number of documents are not useful in many cases, so we ignore them. Use a parameter `min_df`
to ignore all terms that occur in strictly fewer than `min_df=10` documents.

Similarly, words that occur in a large *fraction* of the documents don't bring any more information for some tasks. Use a parameter `max_df_ratio` to trim out such words. For example, `max_df_ratio=0.95` means ignore all words that occur in more than 95% of the documents.

As a reminder, we define the IDF statistic as...
$$ IDF(t) = \log \left(\frac{N}{1 + DF(t)} \right) $$

where $N$ is the total number of docs and $DF(t)$ is the number of docs containing $t$. Keep in mind, there are other definitions of IDF out there, so if you go looking for resources on the internet, you might find differing (but also valid) accounts. In practice the base of the log doesn't really matter, however you should use base 2 here.

In [115]:
def compute_idf(inv_idx, n_docs, min_df=10, max_df_ratio=0.95):
    """ Compute term IDF values from the inverted index.
    Words that are too frequent or too infrequent get pruned.
    
    Hint: Make sure to use log base 2.
    
    Arguments
    =========
    
    inv_idx: an inverted index as above
    
    n_docs: int,
        The number of documents.
        
    min_df: int,
        Minimum number of documents a term must occur in.
        Less frequent words get ignored. 
        Documents that appear min_df number of times should be included.
    
    max_df_ratio: float,
        Maximum ratio of documents a term can occur in.
        More frequent words get ignored.
    
    Returns
    =======
    
    idf: dict
        For each term, the dict contains the idf value.
        
    """
    
    idf = {}
    for term in inv_idx:
        if len(inv_idx[term]) >= min_df and len(inv_idx[term])/n_docs <= max_df_ratio:
            idf[term] = round(math.log(n_docs/(1+len(inv_idx[term])),2),2)
    return idf

In [112]:
inv_idx['blah']

[(7439, 3), (12528, 3), (19035, 3), (19043, 3)]

In [116]:
idf_dict = compute_idf(inv_idx, len(flat_msgs))
idf_dict

{'you': 2.06,
 'do': 3.41,
 "n't": 3.52,
 'have': 4.09,
 'your': 4.81,
 'own': 8.15,
 'credit': 9.99,
 'card': 9.17,
 '?': 2.63,
 'i': 1.78,
 'even': 6.7,
 'a': 2.97,
 '.': 0.43,
 'know': 4.42,
 'are': 4.43,
 'such': 8.07,
 'little': 5.74,
 'girl': 8.41,
 "'m": 3.68,
 ',': 1.57,
 'yeah': 5.41,
 'when': 5.7,
 'it': 3.05,
 'comes': 8.82,
 'to': 2.43,
 'that': 3.29,
 'stuff': 8.07,
 "'re": 4.17,
 'feel': 6.19,
 'so': 4.04,
 'bad': 7.59,
 'need': 5.86,
 'like': 3.77,
 'ask': 8.85,
 'me': 4.17,
 'for': 4.36,
 'money': 8.38,
 'too': 7.12,
 'how': 5.36,
 'think': 5.21,
 "'s": 2.67,
 'embarrassing': 9.49,
 'definitely': 7.81,
 'sorry': 8.03,
 'bruce': 6.59,
 'and': 2.98,
 'really': 4.76,
 'want': 4.83,
 'help': 7.5,
 'him': 5.97,
 'out': 5.14,
 'mean': 6.1,
 'man': 8.22,
 'here': 5.16,
 'buy': 9.28,
 'yourself': 8.68,
 'something': 6.68,
 'in': 4.11,
 'the': 2.87,
 'well': 6.39,
 '$': 8.07,
 'on': 4.52,
 'now': 5.7,
 "'ve": 5.83,
 'got': 5.47,
 '!': 4.22,
 'can': 5.39,
 'go': 4.67,
 '...': 4.3

In [84]:
# This is an autograder test. Here we can test the function you just wrote above.
start_time = time.time()
idf_dict = compute_idf(inv_idx, len(flat_msgs))
execution_time = time.time() - start_time

assert len(idf_dict) < len(inv_idx)
assert 'blah' not in idf_dict
assert 'blah' in inv_idx 
assert '.' in idf_dict
assert '3' not in idf_dict
assert idf_dict['bruce'] >= 6.0 and idf_dict['bruce'] <= 7.0
assert idf_dict['baby'] >= 6.0 and idf_dict['baby'] <= 8.0
assert execution_time <= 1.0


### Q6 Compute the norm of each document using the inverted index (Code Completion)<a class="anchor" id="q6"></a>

Recalling our tf-idf vector representation of documents, we can compute the "norm" as the norm (length) of the vector representation of that document. More specifically, the norm of a document $j$, denoted as $\left|\left| d_j \right|\right|$, is given as follows...

$$ \left|\left| d_j \right|\right| = \sqrt{\sum_{\text{word } i} (tf_{ij} \cdot idf_i)^2} $$

Once again, this can be quite efficiently implemented using the inverted index. Below, write a function that does this.

In [98]:
def compute_doc_norms(index, idf, n_docs):
    """ Precompute the euclidean norm of each document.
    
    Arguments
    =========
    
    index: the inverted index as above
    
    idf: dict,
        Precomputed idf values for the terms.
    
    n_docs: int,
        The total number of documents.
    
    Returns
    =======
    
    norms: np.array, size: n_docs
        norms[i] = the norm of document i.
    """
    
    norms = np.zeros(n_docs)
    for term in index:
        for i in index[term]:
            if term in idf:
                norms[i[0]] += (i[1]*idf[term])**2
    norms = np.sqrt(norms)
    return norms

In [109]:
doc_norms

array([18.0375913 , 16.78391492,  4.78431813, ..., 35.19907243,
        6.01539691, 13.55259016])

In [96]:
len(flat_msgs)

39678

In [97]:
len(inv_idx)

9662

In [99]:
# This is an autograder test. Here we can test the function you just wrote above.
start_time = time.time()
doc_norms = compute_doc_norms(inv_idx, idf_dict, len(flat_msgs))
execution_time = time.time() - start_time

assert len(flat_msgs) == len(doc_norms)
assert doc_norms[3722] == 0
assert max(doc_norms) < 80
assert doc_norms[1] >= 15.5 and doc_norms[1] <= 17.5
assert doc_norms[5] >= 6.5 and doc_norms[5] <= 8.5
assert execution_time <= 1.0

### Q7 Efficiently compute the dot product *using* the inverted index (Code Completion)<a class="anchor" id="q7"></a>

We are getting closer to being able to use our inverted index to do a fast implementation of cosine similarity. There is one more ingredient that will come in handy when it comes to optimization. Recall the definition of cosine similarity (where ${q}$ is a query tf-idf vector and ${d_j}$ is the tf-idf vector of the ${j}$th document):

$$ cossim(\vec{q}, \vec{d_j}) = \frac{\vec{q} \cdot \vec{d_j}}{\|\vec{q}\| \cdot \|\vec{d_j}\|}$$

Specifically, let's focus on the numerator, which computes a dot product. If we recall the definition of the dot product, this can be written as:

$$ \vec{q} \cdot \vec{d_j} = \sum_{i} {q_i} * {d_i}_j $$

Here ${q_i}$ and ${d_i}_j$ are the $i$-th dimension of the vectors $q$ and ${d_j}$ respectively.
Because many ${q_i}$ and ${d_i}_j$ are zero, it is actually a bit wasteful to actually create the vectors $q$ and $d_j$ as numpy arrays; this is the method that you saw in class.

A faster approach to computing the numerator term (dot product) for cosine similarity involves quickly computing the above summation using the inverted index. Recall from class that this is achieved via a *term-at-a-time* approach, iterating over ${q}_j$ that are nonzero (i.e. ${q}_j$ such that the word $j$ appears in the query) and building up *score accumulators* for each document as you iterate.

In this question, you will write a function that implements this term-at-a-time score accumulation.

In [177]:
def accumulate_dot_scores(query_word_counts, index, idf):
    """ Perform a term-at-a-time iteration to efficiently compute the numerator term of cosine similarity across multiple documents.
    
    Arguments
    =========
    
    query_word_counts: dict,
        A dictionary containing all words that appear in the query;
        Each word is mapped to a count of how many times it appears in the query.
        In other words, query_word_counts[w] = the term frequency of w in the query.
        You may safely assume all words in the dict have been already lowercased.
    
    index: the inverted index as above,
    
    idf: dict,
        Precomputed idf values for the terms.
    
    Returns
    =======
    
    doc_scores: dict
        Dictionary mapping from doc ID to the final accumulated score for that doc
    """
    
    doc_scores = {}
    for word in query_word_counts:
        if word in index:
            for i in index[word]:
                if i[0] not in doc_scores:
                    doc_scores[i[0]] = 0
                doc_scores[i[0]] += round(i[1]*idf[word]*idf[word]*query_word_counts[word],2)
    return doc_scores

In [140]:
example_query_words = {"like": 2, "mother": 1, "daughter": 1}
word = 'like'
i = inv_idx[word][1]
idf_dict[word]

3.77

In [155]:
# This is an autograder test. Here we can test the function you just wrote above.
example_query_words = {"like": 2, "mother": 1, "daughter": 1}
start_time = time.time()
scores = accumulate_dot_scores(example_query_words, inv_idx, idf_dict)
execution_time = time.time() - start_time

assert len(scores) > 3000
assert max(scores.values()) < 220
assert scores[13] > 27 and scores[13] < 30
assert scores[324] > 55 and scores[324] < 58
assert execution_time <= 1.0


### Q8a Find the most similar messages to the quotes (Code Completion)<a class="anchor" id="q8"></a>

The goal of this section is to implement `index_search`, a fast implementation of cosine similarity. You will then test your answer by running the search function using the code provided. Briefly discuss why it worked, or why it might not have worked, for each query.

The goal of `index_search` is to compute the cosine similarity between the query and each document in the dataset. Naively, this computation requires you to compute dot products between the query tf-idf vector $q$ and each document's tf-idf vector $d_i$, which sounds very computationally expensive!

Thankfully, you should be able to use the sparsity of the tf-idf representation and the data structures you created to your advantage. We have already laid down all the groundwork we need for this in the previous questions---all that is left to do here is to put it all together!

Once again, recall that our goal is to compute the cosine similarity:

$$ cossim(\vec{q}, \vec{d_j}) = \frac{\vec{q} \cdot \vec{d_j}}{\|\vec{q}\| \cdot \|\vec{d_j}\|}$$

Just to recap, thus far we have created the following:
- An inverted index mapping from word to the documents they appear in
- IDF values for every word that does not appear too rarely or too frequently
- Vector norms for the tf-idf vectors of every document
- A function that uses term-at-a-time iteration to efficiently compute dot products between the query and multiple documents (that is, the numerator of the cosine similarity)

Your task in this function will be to assemble the above components to compute the cosine similarities between the query and documents, and use these to rank the documents.

**Note:** Convert the query to lowercase, and use the `nltk.tokenize.TreebankWordTokenizer` to tokenize the query (provided to you as the `tokenizer` parameter). The transcripts have already been tokenized this way. <br>

**Note 2:** For `index_search`, you need not remove punctuation tokens from the tokenized query before searching.

**Aside:** Precomputation

In many settings, we will need to repeat the same kind of operation many times. Often, part of the input doesn't change.
Queries against the Kardashians transcript are like this: we want to run more queries (in the real world we'd want to run a lot of them every second, even) but the data we are searching doesn't change.

We could write an `index_search` function which taking the `query` and the `msgs` as input, and the function would look like:

    def index_search(query, msgs):
        inv_idx = build_inverted_index(msgs)
        idf = compute_idf(inv_idx, len(msgs))
        doc_norms = compute_doc_norms(inv_idx)
        # do actual search


But notice that the first three lines only depend on the messages. Imagine if we run this a million times with different queries but the same collection of documents: we'd wastefully recompute the index, the IDFs and the norms every time and discard them. It's a better idea, then, to precompute them just once, and pass them as arguments.

In [142]:
inv_idx = build_inverted_index(flat_msgs)

idf = compute_idf(inv_idx, len(flat_msgs),
                  min_df=10,
                  max_df_ratio=0.1)  # documents are very short so we can use a small value here
                                     # examine the actual DF values of common words like "the"
                                     # to set these values

inv_idx = {key: val for key, val in inv_idx.items()
           if key in idf}            # prune the terms left out by idf

doc_norms = compute_doc_norms(inv_idx, idf, len(flat_msgs))

In [198]:
idf

{'do': 3.41,
 "n't": 3.52,
 'have': 4.09,
 'your': 4.81,
 'own': 8.15,
 'credit': 9.99,
 'card': 9.17,
 'even': 6.7,
 'know': 4.42,
 'are': 4.43,
 'such': 8.07,
 'little': 5.74,
 'girl': 8.41,
 "'m": 3.68,
 'yeah': 5.41,
 'when': 5.7,
 'comes': 8.82,
 'stuff': 8.07,
 "'re": 4.17,
 'feel': 6.19,
 'so': 4.04,
 'bad': 7.59,
 'need': 5.86,
 'like': 3.77,
 'ask': 8.85,
 'me': 4.17,
 'for': 4.36,
 'money': 8.38,
 'too': 7.12,
 'how': 5.36,
 'think': 5.21,
 'embarrassing': 9.49,
 'definitely': 7.81,
 'sorry': 8.03,
 'bruce': 6.59,
 'really': 4.76,
 'want': 4.83,
 'help': 7.5,
 'him': 5.97,
 'out': 5.14,
 'mean': 6.1,
 'man': 8.22,
 'here': 5.16,
 'buy': 9.28,
 'yourself': 8.68,
 'something': 6.68,
 'in': 4.11,
 'well': 6.39,
 '$': 8.07,
 'on': 4.52,
 'now': 5.7,
 "'ve": 5.83,
 'got': 5.47,
 '!': 4.22,
 'can': 5.39,
 'go': 4.67,
 '...': 4.32,
 'my': 3.89,
 'god': 6.63,
 'rich': 10.69,
 'then': 6.9,
 'if': 5.34,
 'could': 6.69,
 'take': 6.38,
 'dash': 9.11,
 'maybe': 7.64,
 'tomorrow': 9.17,
 '

In [201]:
def index_search(query, index, idf, doc_norms, score_func=accumulate_dot_scores, tokenizer=treebank_tokenizer):
    """ Search the collection of documents for the given query
    
    Arguments
    =========
    
    query: string,
        The query we are looking for.
    
    index: an inverted index as above
    
    idf: idf values precomputed as above
    
    doc_norms: document norms as computed above
    
    score_func: function,
        A function that computes the numerator term of cosine similarity (the dot product) for all documents.
        Takes as input a dictionary of query word counts, the inverted index, and precomputed idf values.
        (See Q7)
    
    tokenizer: a TreebankWordTokenizer
    
    Returns
    =======
    
    results, list of tuples (score, doc_id)
        Sorted list of results such that the first element has
        the highest score, and `doc_id` points to the document
        with the highest score.
    
    Note: 
        
    """
    query = (query).lower()
    query_words = tokenizer.tokenize(query)
    print(query_words)
    query_word_counts = Counter(query_words)
    
    q_norm = 0
    
    for i in query_word_counts:
        if i in idf:
            q_norm += (query_word_counts[i] * idf[i] )**2
    q_norm = np.sqrt(q_norm)

    doc_scores = score_func(query_word_counts, index, idf)

    results = []
    for i in doc_scores:
        results.append((doc_scores[i]/(q_norm * doc_norms[i]), i))
    results.sort(reverse=True)
    return results


['it', "'s", 'like', 'a', 'bunch', 'of', 'people', 'running', 'around', 'talking', 'about', 'nothing', '.']
22.973010251162123


[(1.0000015158428315, 11048),
 (0.6147130162930822, 18866),
 (0.4615282164776256, 4816),
 (0.4615282164776256, 4567),
 (0.43436963850600685, 17472),
 (0.4203400985219635, 4751),
 (0.4203400985219635, 4515),
 (0.40810750476512175, 17014),
 (0.4056640330883629, 12315),
 (0.40297730337724086, 22667),
 (0.3902961405665085, 34013),
 (0.38826142784914097, 4973),
 (0.38728951577119675, 2524),
 (0.3856913160562376, 24787),
 (0.38461219248003325, 18260),
 (0.3731194140650953, 12316),
 (0.3714684105395907, 28979),
 (0.3612935313768961, 37311),
 (0.3612935313768961, 34937),
 (0.3612935313768961, 34936),
 (0.3612935313768961, 29373),
 (0.3612935313768961, 29371),
 (0.3612935313768961, 29370),
 (0.3612935313768961, 29369),
 (0.3612935313768961, 28282),
 (0.3612935313768961, 26255),
 (0.3612935313768961, 25685),
 (0.3612935313768961, 24654),
 (0.3612935313768961, 24549),
 (0.3612935313768961, 17199),
 (0.3612935313768961, 17195),
 (0.3612935313768961, 965),
 (0.3612935313768961, 289),
 (0.3567846826

In [202]:
# This is an autograder test. Here we can test the function you just wrote above.
start_time = time.time()
results = index_search(queries[1], inv_idx, idf, doc_norms)
execution_time = time.time() - start_time

assert type(results[0]) == tuple
assert max(results)[0] == results[0][0]
assert results[0][0] >= 0.4 and results[0][0] <= 0.48
assert execution_time <= 1.0


for query in queries:
    print("#" * len(query))
    print(query)
    print("#" * len(query))

    for score, msg_id in index_search(query, inv_idx, idf, doc_norms)[:10]:
        print("[{:.2f}] {}: {}\n\t({})".format(
            score,
            flat_msgs[msg_id]['speaker'],
            flat_msgs[msg_id]['text'],
            flat_msgs[msg_id]['episode_title'])) 
    print()

['never', 'say', 'to', 'a', 'famous', 'person', 'that', 'this', 'possible', 'endorsment', 'would', 'bring', "'er", 'to', 'the', 'spot', 'light', '.']
22.404035350802317
#################################################################
It's like a bunch of people running around talking about nothing.
#################################################################
['it', "'s", 'like', 'a', 'bunch', 'of', 'people', 'running', 'around', 'talking', 'about', 'nothing', '.']
22.973010251162123
[1.00] BRUCE: It's like a bunch of people running around talking about nothing.
	(Keeping Up With the Kardashians - Kourt's First Cover)
[0.61] KRIS: It's not a bunch of teenagers running around.
	(Keeping Up With the Kardashians - Kris ``The Cougar'' Jenner)
[0.46] ROB: I have a bunch of connections in the industry.
	(Keeping Up With the Kardashians - Must Love Dogs)
[0.46] ROB: I have a bunch of connections in the industry.
	(Keeping Up With the Kardashians - Must Love Dogs)
[0.43] KHLOE: She's, lik

### Q8b Find the most similar messages to the quotes (Free Response)<a class="anchor" id="q8b"></a>

Briefly discuss why cosine similarity worked, or why it might not have worked, **for each query**.

<div style="border-bottom: 4px solid #AAA; padding-bottom: 6px; font-size: 16px; font-weight: bold;">Write your answer in the provided cell below</div>

YOUR ANSWER HERE

<div style="border-top: 4px solid #AAA; padding-bottom: 6px; font-size: 16px; font-weight: bold; text-align: center;"></div>

- - -
<p style='text-align:right; font-size:11px'>[[contents](#contents)]</p>

# Extra Credit (Optional)<a class="anchor" id="ec"></a>

### Q9EC (optional)<a class="anchor" id="q9"></a>

### Finding your own similarity metric

We've explored using cosine similarity and edit distance to find similar messages to input queries. However, there's a whole world of ways to measure the similarity between two documents. Go forth, and research!

(Fun fact: Fundamental information retrieval techniques were in fact developed at Cornell, so you would not be the first Cornellian to disrupt the field)

For this question, find a new way of measuring similarity between two documents, and implement a search using your new metric. Your new way of measuring document similarity should be different enough from the two approaches we already implemented. It can be a method you devise or an existing method from somewhere else (make sure to reveal your sources).

**Note:** The amount of EC awarded for this question will be determined based on creativity, originality, implementation, and analysis. *Do not delete the cell below.*

In [ ]:
# YOUR CODE HERE
raise NotImplementedError()